In [1]:
import json, csv, datetime, pytz, math
import pandas as pd, numpy as np
import plotly.graph_objects as go

In [2]:
# import csv price data
ohlc = {
    "btcusd": pd.read_csv(r"data/BTCUSD.csv"),
    "ethusd": pd.read_csv(r"data/ETHUSD.csv"),
    "ethbtc": pd.read_csv(r"data/ETHBTC.csv")
}

# reformat datetime and set as index
for key in ohlc.keys():
    ohlc[key]["timestamp"] = ohlc[key]["timestamp"].astype("datetime64[ns, UTC]")
    ohlc[key].set_index("timestamp", inplace = True)

# init parameters for analysis
inputs = {
    "init c-ratio": 1.5,
    "courtesy call": 1.25,
    "liquidation": 1.1,
    "start date": datetime.datetime(2021,1,1).replace(tzinfo=pytz.utc),
    "end date": ohlc["btcusd"].index.max()
}

inputs["date_rng"] = pd.date_range(inputs["start date"], inputs["end date"])

In [3]:
# initialize collateralized positions every day at open
def create_position(inputs, date, btcusd, ethusd):
    eth_required = btcusd * inputs["init c-ratio"] / ethusd
    position = {
        "timestamp": [date],
        "eth posted": [eth_required],
        "underlying value": [btcusd], # 1 btc positions
        "collateral value": [eth_required * ethusd],
        "c-ratio": [inputs["init c-ratio"]]
    }
    return position

# update position with new items in array and recalculate c-ratio
def update_position(position, date, btcusd, ethusd):
    eth_required = position["eth posted"][0]
    position["timestamp"].append(date)
    position["eth posted"].append(eth_required) # no change
    position["underlying value"].append(btcusd)
    position["collateral value"].append(eth_required * ethusd)
    position["c-ratio"].append(eth_required * ethusd / btcusd)
    return position

In [4]:
test = {}
benchmarks = {"init c-ratio":[],"courtesy call":[],"liquidation":[]}

for t in inputs["date_rng"]:
    for key in benchmarks.keys():
        benchmarks[key].append(inputs[key])
    btcusd = ohlc["btcusd"]["open"].at[t]
    ethusd = ohlc["ethusd"]["open"].at[t]
    # i want to use this, but haven't figured out how yet
    ethbtc = ohlc["ethbtc"]["open"].at[t]
    # update all positions
    for key in test.keys():
        test[key] = update_position(test[key], t, btcusd, ethusd)
    # create a new position
    test[t] = create_position(inputs, t, btcusd, ethusd)

In [5]:

fig = go.Figure()

for date, position in test.items():
    fig.add_trace(
        go.Scatter(
            x = position["timestamp"],
            y = position["c-ratio"],
            mode = "lines"
            #name = position["timestamp"][0].format("%Y-%m-%d")
        ))
    
fig.add_trace(go.Scatter(x = inputs["date_rng"], y = benchmarks["init c-ratio"], line_color = "green", mode = "lines", name = "init c-ratio"))
fig.add_trace(go.Scatter(x = inputs["date_rng"], y = benchmarks["courtesy call"], line_color = "orange", mode = "lines", name = "courtesy call"))
fig.add_trace(go.Scatter(x = inputs["date_rng"], y = benchmarks["liquidation"], line_color = "red", mode = "lines", name = "liquidation"))
fig.show()